In [2]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from scipy.integrate import solve_ivp
from IPython.display import HTML, display

# Parámetros
g = float(input("Gravedad (m/s²): "))
L = float(input("Longitud del péndulo (m): "))
b = float(input("Coef. de amortiguamiento: "))
theta0 = float(input("Ángulo inicial (grados): "))
omega0 = 0.0

theta0_rad = np.radians(theta0)

# Ecuación del péndulo
def pendulum(t, z):
    theta, omega = z
    return [omega, -b * omega - (g / L) * np.sin(theta)]

# Evento para detener la simulación
def stop_event(t, z):
    return max(abs(z[0]), abs(z[1])) - 1e-3

stop_event.terminal = True
stop_event.direction = -1

# Simulación
z0 = [theta0_rad, omega0]
sol = solve_ivp(pendulum, (0, 100), z0, events=stop_event, max_step=0.01, rtol=1e-8)
theta, omega, t = sol.y[0], sol.y[1], sol.t

# Posición
x, y = L * np.sin(theta), -L * np.cos(theta)

# Conteo de oscilaciones
crossings = np.where(np.diff(np.sign(theta)))[0]
osc_times = t[crossings]
osc_count = np.array([np.sum(osc_times <= ti) * 0.5 for ti in t], dtype=int)

print(f"\n🔁 Oscilaciones completas: {int(osc_count[-1])}")
print(f"🕒 Tiempo total: {t[-1]:.2f} s\n")

# Animación
fig, ax = plt.subplots(figsize=(5, 5))
ax.set_xlim(-L - 0.2, L + 0.2)
ax.set_ylim(-L - 0.2, L + 0.2)
ax.set_aspect('equal')
ax.grid()

line, = ax.plot([], [], 'o-', lw=2)
info = ax.text(0.05, 0.9, '', transform=ax.transAxes)

def init():
    line.set_data([], [])
    info.set_text('')
    return line, info

def animate(i):
    line.set_data([0, x[i]], [0, y[i]])
    info.set_text(f"Tiempo = {t[i]:.2f} s\nOscilaciones = {osc_count[i]}")
    return line, info

ani = FuncAnimation(fig, animate, frames=len(t), init_func=init, interval=10)
plt.close(fig)
display(HTML(ani.to_html5_video()))

Gravedad (m/s²): 9.81
Longitud del péndulo (m): 1.5
Coef. de amortiguamiento: 0.75
Ángulo inicial (grados): 30

🔁 Oscilaciones completas: 7
🕒 Tiempo total: 17.22 s

